In [1]:
%pip install pandas
%pip install scikit-learn

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.0 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.0 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import pandas as pd
from sklearn.naive_bayes import MultinomialNB
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline
import joblib
import os

df = pd.read_csv("activity_labels.csv")

output_dir = "/mnt/data"
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

df.to_csv(os.path.join(output_dir, "activity_description.csv"))

!cp /mnt/data/activity_descriptions.csv /mnt/data/activity_description.csv

'cp' is not recognized as an internal or external command,
operable program or batch file.


In [3]:
from sklearn.base import BaseEstimator, TransformerMixin
# import nltk
# from nltk.stem import WordNetLemmatizer
# nltk.download('wordnet')

# class LemmaTokenizer:
#   def __init__(self):
#     self.wnl = WordNetLemmatizer()
#   def __call__(self, doc):
#     return [self.wnl.lemmatize(t) for t in doc.split()]

In [4]:
from tokenizer import LemmaTokenizer

vectorizer = TfidfVectorizer(ngram_range = (1, 2),tokenizer=LemmaTokenizer(), stop_words= 'english')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\joeke\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [5]:
pipeline = Pipeline([
    ("tfidf", vectorizer),
    ("model", MultinomialNB())
])

In [6]:
pipeline.get_params()

{'memory': None,
 'steps': [('tfidf',
   TfidfVectorizer(ngram_range=(1, 2), stop_words='english',
                   tokenizer=<tokenizer.LemmaTokenizer object at 0x00000219D9558E60>)),
  ('model', MultinomialNB())],
 'transform_input': None,
 'verbose': False,
 'tfidf': TfidfVectorizer(ngram_range=(1, 2), stop_words='english',
                 tokenizer=<tokenizer.LemmaTokenizer object at 0x00000219D9558E60>),
 'model': MultinomialNB(),
 'tfidf__analyzer': 'word',
 'tfidf__binary': False,
 'tfidf__decode_error': 'strict',
 'tfidf__dtype': numpy.float64,
 'tfidf__encoding': 'utf-8',
 'tfidf__input': 'content',
 'tfidf__lowercase': True,
 'tfidf__max_df': 1.0,
 'tfidf__max_features': None,
 'tfidf__min_df': 1,
 'tfidf__ngram_range': (1, 2),
 'tfidf__norm': 'l2',
 'tfidf__preprocessor': None,
 'tfidf__smooth_idf': True,
 'tfidf__stop_words': 'english',
 'tfidf__strip_accents': None,
 'tfidf__sublinear_tf': False,
 'tfidf__token_pattern': '(?u)\\b\\w\\w+\\b',
 'tfidf__tokenizer': <tokeni

In [7]:
from sklearn.model_selection import GridSearchCV

params = {
    'tfidf__max_df': [0.5, 0.75, 1.0],
    'tfidf__min_df': [1, 2, 5, 10], 
    'tfidf__ngram_range': [(1, 1), (1, 2), (1, 3)], 
    'tfidf__use_idf': [True, False], 
    'tfidf__smooth_idf': [True, False], 
    'tfidf__sublinear_tf': [True, False], 
    'model__alpha': [0.01, 0.1, 0.5, 1, 5]
}

In [8]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(df["Description"], df["Label"], test_size=0.2, random_state=42, stratify=df["Label"])

grid = GridSearchCV(pipeline, param_grid=params, cv=5, scoring='accuracy')
grid.fit(X_train, y_train)

c:\Users\joeke\OneDrive\Documents\Kuliah\Sem4\ML\Model\venv\Lib\site-packages\sklearn\feature_extraction\text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
c:\Users\joeke\OneDrive\Documents\Kuliah\Sem4\ML\Model\venv\Lib\site-packages\sklearn\feature_extraction\text.py:402: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['ha', 'u', 'wa'] not in stop_words.
  warnings.warn(
c:\Users\joeke\OneDrive\Documents\Kuliah\Sem4\ML\Model\venv\Lib\site-packages\sklearn\feature_extraction\text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
c:\Users\joeke\OneDrive\Documents\Kuliah\Sem4\ML\Model\venv\Lib\site-packages\sklearn\feature_extraction\text.py:402: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['ha', 'u', 'wa'] not in

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('tfidf',
                                        TfidfVectorizer(ngram_range=(1, 2),
                                                        stop_words='english',
                                                        tokenizer=<tokenizer.LemmaTokenizer object at 0x00000219D9558E60>)),
                                       ('model', MultinomialNB())]),
             param_grid={'model__alpha': [0.01, 0.1, 0.5, 1, 5],
                         'tfidf__max_df': [0.5, 0.75, 1.0],
                         'tfidf__min_df': [1, 2, 5, 10],
                         'tfidf__ngram_range': [(1, 1), (1, 2), (1, 3)],
                         'tfidf__smooth_idf': [True, False],
                         'tfidf__sublinear_tf': [True, False],
                         'tfidf__use_idf': [True, False]},
             scoring='accuracy')

In [9]:
grid.best_score_

np.float64(0.5887681159420289)

In [10]:
grid.best_params_

{'model__alpha': 0.5,
 'tfidf__max_df': 0.5,
 'tfidf__min_df': 1,
 'tfidf__ngram_range': (1, 3),
 'tfidf__smooth_idf': True,
 'tfidf__sublinear_tf': True,
 'tfidf__use_idf': True}

In [11]:
from sklearn.metrics import classification_report

y_pred = grid.predict(X_test)
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

       heavy       0.44      0.40      0.42        10
       light       0.62      0.73      0.67        11
      medium       0.38      0.33      0.35         9

    accuracy                           0.50        30
   macro avg       0.48      0.49      0.48        30
weighted avg       0.49      0.50      0.49        30



In [12]:
joblib.dump(grid, "activity_pipeline.pkl")
joblib.dump(vectorizer, 'vectorizer.pkl')

['vectorizer.pkl']

In [13]:
import pickle

grid = joblib.load("activity_pipeline.pkl")
vectorizer = joblib.load('vectorizer.pkl')

new_activities = [
    "Delivered packages using a vehicle",  
    "Ran a marathon",                      
    "Watched Netflix all day",
    "i go for a jog in the morning, and go to school for 6 hours, and i sleep for 8 hours",
    "watch people go for a jog and read books",
    "I wake up at 7:00 AM and immediately head to the bathroom. After getting ready, I have a light breakfast like toast and coffee. By 8:00 AM, I'm out the door, riding my motorcycle to the office. I usually arrive around 8:30 AM, enough time to get my coffee and prepare for the day. My work hours are from 9:00 AM to 5:00 PM, with a lunch break around 12:30 PM. After work, I'll often meet up with a friend for dinner, maybe try a new local restaurant. I usually get home by 7:00 PM. In the evening, I like to relax, maybe watch a movie or read a book. I'm usually in bed by 11:00 PM."
]

predictions = grid.predict(new_activities)

for text, label in zip(new_activities, predictions):
    print(f"Activity: '{text}' => Intensity: {label}")

Activity: 'Delivered packages using a vehicle' => Intensity: light
Activity: 'Ran a marathon' => Intensity: heavy
Activity: 'Watched Netflix all day' => Intensity: light
Activity: 'i go for a jog in the morning, and go to school for 6 hours, and i sleep for 8 hours' => Intensity: light
Activity: 'watch people go for a jog and read books' => Intensity: light
Activity: 'I wake up at 7:00 AM and immediately head to the bathroom. After getting ready, I have a light breakfast like toast and coffee. By 8:00 AM, I'm out the door, riding my motorcycle to the office. I usually arrive around 8:30 AM, enough time to get my coffee and prepare for the day. My work hours are from 9:00 AM to 5:00 PM, with a lunch break around 12:30 PM. After work, I'll often meet up with a friend for dinner, maybe try a new local restaurant. I usually get home by 7:00 PM. In the evening, I like to relax, maybe watch a movie or read a book. I'm usually in bed by 11:00 PM.' => Intensity: light


c:\Users\joeke\OneDrive\Documents\Kuliah\Sem4\ML\Model\venv\Lib\site-packages\sklearn\feature_extraction\text.py:402: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['ha', 'u', 'wa'] not in stop_words.
  warnings.warn(
